### Определение координат границы между между Россией и Украиной

In [ ]:
#Библиотека для работы с многомерными массивами
!pip install numpy
#Библиотека для обработки и анализа данных
!pip install pandas
#Библиотека для библиотека для визуализации данных
!pip install plotly
#Библиотека для упрощения работы с геопространственными данными
!pip install geopandas 

In [ ]:
# Импорт библиотек для работы с данными
import json
import pandas as pd
import numpy as np

In [5]:
# Считываем файл с координатами всех регионов
with open('data//gadm41_RUS_1.json', encoding = 'utf-8') as js:
    dict_coordin_border = json.load(js)

In [6]:
for regions in dict_coordin_border['features']:
    print(regions['properties']['NL_NAME_1'])

{'type': 'FeatureCollection',
 'name': 'gadm41_RUS_1',
 'crs': {'type': 'name',
  'properties': {'name': 'urn:ogc:def:crs:OGC:1.3:CRS84'}},
 'features': [{'type': 'Feature',
   'properties': {'GID_1': 'RUS.1_1',
    'GID_0': 'RUS',
    'COUNTRY': 'Russia',
    'NAME_1': 'Adygey',
    'VARNAME_1': 'Adygea|Adygeya|Adygheya|Republic',
    'NL_NAME_1': 'РеспубликаАдыгея',
    'TYPE_1': 'Respublika',
    'ENGTYPE_1': 'Republic',
    'CC_1': 'NA',
    'HASC_1': 'RU.AD',
    'ISO_1': 'NA'},
   'geometry': {'type': 'MultiPolygon',
    'coordinates': [[[[40.3872, 44.6721],
       [40.375, 44.6423],
       [40.3606, 44.6142],
       [40.3565, 44.5881],
       [40.375, 44.5635],
       [40.4021, 44.5355],
       [40.4151, 44.5161],
       [40.4273, 44.4786],
       [40.4525, 44.4429],
       [40.4838, 44.4024],
       [40.5004, 44.3591],
       [40.4937, 44.3224],
       [40.4753, 44.2956],
       [40.426, 44.2494],
       [40.4188, 44.2171],
       [40.4163, 44.1881],
       [40.4177, 44.1563],


### Нахождение координат точек границ соседних с Украиной регионов

In [7]:
"""
Выбираем субъекты федерации, которые граничат с Украиной:
1. Воронежская область
2. Брянская область
3. Курская область
4. Ростовская область
5. Белгородская область
"""

#Создаем dataframe для записи данных
df_coord_reg = pd.DataFrame()
sequence_number = 0

for regions in dict_coordin_border['features']:
    #Ставим условия для поля названия субъектов
    if regions['properties']['NL_NAME_1'] in ['Воронежскаяобласть','Брянскаяобласть','Курскаяобласть','Ростовскаяобласть', 'Белгородскаяобласть']:
        for list_coordin_lv_1 in regions['geometry']['coordinates']:
            for list_coordin_lv_2 in list_coordin_lv_1:
                for list_coordin_finish_lvl in list_coordin_lv_2:
                    #Заполняем df: Название региона, координаты точки границы, порядковый номер записи, цвет региона
                    if regions['properties']['NL_NAME_1'] == 'Воронежскаяобласть': color = 'white'
                    if regions['properties']['NL_NAME_1'] == 'Брянскаяобласть': color = 'blue'
                    if regions['properties']['NL_NAME_1'] == 'Курскаяобласть': color = 'red'
                    if regions['properties']['NL_NAME_1'] == 'Ростовскаяобласть': color = 'yellow'
                    if regions['properties']['NL_NAME_1'] == 'Белгородскаяобласть': color = 'purple'
                        
                    df_coord_reg = df_coord_reg.append({'region': regions['properties']['NL_NAME_1'], #Название региона
                                                        'lon': list_coordin_finish_lvl[0], #Долгота точки границы
                                                        'lat': list_coordin_finish_lvl[1], #Широта точки границы
                                                        'sequence_number': str(sequence_number), #Порядковый номер записи
                                                        'color': color}, #Цвет региона 
                                                       ignore_index = True)
                    sequence_number += 1

In [8]:
#Посмотрим на получившийся df
df_coord_reg

region      lon      lat sequence_number   color
0     Белгородскаяобласть  39.2482  50.1158               0  purple
1     Белгородскаяобласть  39.2858  50.0916               1  purple
2     Белгородскаяобласть  39.3360  50.0704               2  purple
3     Белгородскаяобласть  39.3649  50.0454               3  purple
4     Белгородскаяобласть  39.3743  49.9940               4  purple
...                   ...      ...      ...             ...     ...
3158   Воронежскаяобласть  39.2647  49.8441            3158   white
3159   Воронежскаяобласть  39.2916  49.8500            3159   white
3160   Воронежскаяобласть  39.3008  49.8961            3160   white
3161   Воронежскаяобласть  39.3157  49.9306            3161   white
3162   Воронежскаяобласть  39.3391  49.9661            3162   white

[3163 rows x 5 columns]

### Визуализируем полученные данные на карте Европы и выберим нужные точки границы

In [9]:
#Импортируем библиотеки для визуализации данных
from plotly.graph_objs import Scatter, Figure, Layout
import plotly
import plotly.graph_objs as go
import geopandas as gpd

In [14]:
#Визуализируем на карте точки с координатами для проверки и дальнейшего анализа

fig = go.Figure(data=go.Scattergeo( #Scattergeo - данные, визуализируемые в виде точек географической карте
                  lon = df_coord_reg['lon'],                                               #Долгота точки
                  lat = df_coord_reg['lat'],                                               #Широта точки
                  mode = 'markers',                                                        #Вид точки
                  marker_color  = df_coord_reg['color'],                                   #Цвет точки
                  text = df_coord_reg['region'] + ' ' + df_coord_reg['sequence_number']    #Текст при наведении
                )
            )

fig.update_layout(
        title = 'Субъекты РФ граничащие с Украиной ',      #Задаем название карты
        geo = dict(
            scope='europe',                                #Область карты 
            landcolor = "green",                           #Цвет для стран
            countrycolor = "black",                        #Граница стран
        ),
    )

In [15]:
#Исходя из карты, выбираем следующие срезы df и записываем их в новую переменную 
df_coord_border = pd.concat([df_coord_reg[11:411], 
                             df_coord_reg[1278:1459], 
                             df_coord_reg[974:1226], 
                             df_coord_reg[3084:3157],
                             df_coord_reg[2004:2413]])

In [26]:
df_coord_border

region      lon      lat sequence_number   color
11    Белгородскаяобласть  39.2300  49.8384              11  purple
12    Белгородскаяобласть  39.2218  49.8444              12  purple
13    Белгородскаяобласть  39.2224  49.8498              13  purple
14    Белгородскаяобласть  39.2136  49.8503              14  purple
15    Белгородскаяобласть  39.2142  49.8557              15  purple
...                   ...      ...      ...             ...     ...
2408    Ростовскаяобласть  40.1633  49.4581            2408  yellow
2409    Ростовскаяобласть  40.1850  49.4758            2409  yellow
2410    Ростовскаяобласть  40.1978  49.4909            2410  yellow
2411    Ростовскаяобласть  40.2174  49.5070            2411  yellow
2412    Ростовскаяобласть  40.2181  49.5152            2412  yellow

[1315 rows x 5 columns]

### Визуально проверяем полученный dataframe 

In [27]:
fig = go.Figure(data=go.Scattergeo(lon = df_coord_border['lon'], 
                                   lat = df_coord_border['lat'], 
                                   mode = 'markers',
                                   marker_color  = df_coord_border['color'],
                                   text = df_coord_border['region'] + ' ' + df_coord_border['sequence_number']))
fig.update_layout(
        title = 'Граница между Россией и Украиной',
        geo = dict(
            scope='europe',                                #Область карты 
            landcolor = "green",                           #Цвет для стран
            countrycolor = "black",                        #Граница стран
        ),
    )

In [ ]:
#Сохраняем данные в json
df_coord_border[['lon', 'lat']].to_json('data//border.json')